In [21]:
from WBT.whitebox_tools import WhiteboxTools
import rasterio
import os
import matplotlib.pyplot as plt
import numpy as np
import shutil
import math
import time

wbt = WhiteboxTools()

In [2]:
os.chdir(r'C:\\Users\\sasha\\abstract_surfaces\\')

In [5]:
entries = os.listdir('./surfaces/')
entries

['clear', 'noisy']

In [10]:
clear_dems = os.listdir('./surfaces/' + entries[0])
noisy_dems = os.listdir('./surfaces/' + entries[1])

print(f'Clear dems: {clear_dems}', f'Noisy dems: {noisy_dems}', sep='\n\n')

Clear dems: ['hemicylinder_clear.tif', 'hemisphere_clear.tif', 'inclined_clear.tif', 'paraboloid_clear.tif']

Noisy dems: ['hemicylinder_n_05.tif', 'hemicylinder_n_1.tif', 'hemicylinder_n_2.tif', 'hemicylinder_un_05.tif', 'hemicylinder_un_1.tif', 'hemicylinder_un_2.tif', 'hemisphere_n_05.tif', 'hemisphere_n_1.tif', 'hemisphere_n_2.tif', 'hemisphere_un_05.tif', 'hemisphere_un_1.tif', 'hemisphere_un_2.tif', 'inclined_n_05.tif', 'inclined_n_1.tif', 'inclined_n_2.tif', 'inclined_un_05.tif', 'inclined_un_1.tif', 'inclined_un_2.tif', 'paraboloid_n_05.tif', 'paraboloid_n_1.tif', 'paraboloid_n_2.tif', 'paraboloid_un_05.tif', 'paraboloid_un_1.tif', 'paraboloid_un_2.tif']


In [11]:
arr_clear_dems = []
for clear_dem in clear_dems:
    
    tmp_path = r'C:\Users\sasha\abstract_surfaces\surfaces\clear\\' + clear_dem
    #print(tmp_path)
    
    with rasterio.open(tmp_path, 'r') as ds:
        arr_in = ds.read()
    #arr_clear_dems[clear_dem] = arr_in[0]
    arr_clear_dems.append(arr_in[0])
    #plt.imshow(arr_noisy_dems[-1], cmap='binary')
    #plt.show()
    print(f'Appended {clear_dem}')

Appended hemicylinder_clear.tif
Appended hemisphere_clear.tif
Appended inclined_clear.tif
Appended paraboloid_clear.tif


In [12]:
arr_noisy_dems = []
for noisy_dem in noisy_dems:
    
    tmp_path = r'C:\Users\sasha\abstract_surfaces\surfaces\noisy\\' + noisy_dem
    #print(tmp_path)
    
    with rasterio.open(tmp_path, 'r') as ds:
        arr_in = ds.read()
    #arr_noisy_dems[noisy_dem] = arr_in[0]
    arr_noisy_dems.append(arr_in[0])
    #plt.imshow(arr_noisy_dems[-1], cmap='binary')
    #plt.show()
    print(f'Appended {noisy_dem}')

Appended hemicylinder_n_05.tif
Appended hemicylinder_n_1.tif
Appended hemicylinder_n_2.tif
Appended hemicylinder_un_05.tif
Appended hemicylinder_un_1.tif
Appended hemicylinder_un_2.tif
Appended hemisphere_n_05.tif
Appended hemisphere_n_1.tif
Appended hemisphere_n_2.tif
Appended hemisphere_un_05.tif
Appended hemisphere_un_1.tif
Appended hemisphere_un_2.tif
Appended inclined_n_05.tif
Appended inclined_n_1.tif
Appended inclined_n_2.tif
Appended inclined_un_05.tif
Appended inclined_un_1.tif
Appended inclined_un_2.tif
Appended paraboloid_n_05.tif
Appended paraboloid_n_1.tif
Appended paraboloid_n_2.tif
Appended paraboloid_un_05.tif
Appended paraboloid_un_1.tif
Appended paraboloid_un_2.tif


In [13]:
#len(arr_noisy_dems)

In [39]:
arr_filtered_dems = []
best_filter = {}

start_time = time.time()

with open(r'C:\Users\sasha\abstract_surfaces\surfaces\results.txt', 'w+') as file:

    for noisy_dem in noisy_dems:
        
        file.write('---\n' + noisy_dem + '\n')
        
        clear_path = r'C:\Users\sasha\abstract_surfaces\surfaces\clear\\' + noisy_dem.split('_')[0] + '_clear.tif'
        tmp_path = r'C:\Users\sasha\abstract_surfaces\surfaces\noisy\\' + noisy_dem
        output_path = r'C:\Users\sasha\abstract_surfaces\surfaces\current_' + noisy_dem.split('_')[0] + '.tif'
        #good_path = r'C:\Users\sasha\abstract_surfaces\surfaces\best_' + noisy_dem.split('_')[0] + '.tif'

        with rasterio.open(clear_path, 'r') as ds:
            data_clear = ds.read()
            data_clear = data_clear[0] 

        with rasterio.open(tmp_path, 'r') as ds:
            data_noisy = ds.read()
            data_noisy = data_noisy[0]    

        min_mean = 99999

        wbt.verbose = True

        # - - -
        #MeanFilter
        for filt_xy in [3, 5, 7]:
            wbt.mean_filter(
                i = tmp_path, 
                output = output_path, 
                filterx=filt_xy, 
                filtery=filt_xy
            )

            with rasterio.open(output_path, 'r') as ds:
                data_filt = ds.read()
                data_filt = data_filt[0]

            if abs(np.mean(np.subtract(data_clear, data_filt))) < min_mean:
                best_filter.update({noisy_dem : ['MeanFilter', filt_xy, filt_xy]})
                min_mean = abs(np.mean(np.subtract(data_clear, data_filt)))

            file.write('\t' + f'MeanFilter: {filt_xy} * {filt_xy}. ' + f'mean = {np.mean(np.subtract(data_clear, data_filt))}' + '\n')

        # - - -
        #MedianFilter
        for filt_xy in [3, 5, 7]:
            wbt.median_filter(
                i = tmp_path, 
                output = output_path, 
                filterx=filt_xy, 
                filtery=filt_xy,
                sig_digits=2
            )

            with rasterio.open(output_path, 'r') as ds:
                data_filt = ds.read()
                data_filt = data_filt[0]

            if abs(np.mean(np.subtract(data_clear, data_filt))) < min_mean:
                best_filter.update({noisy_dem : ['MedianFilter', filt_xy, filt_xy]})
                min_mean = abs(np.mean(np.subtract(data_clear, data_filt)))

            file.write('\t' + f'MedianFilter: {filt_xy} * {filt_xy}. ' + f'mean = {np.mean(np.subtract(data_clear, data_filt))}' + '\n')

        # - - -
        #AdaptiveFilter
        for filt_xy in [3, 5, 7]:
            for threshold in np.arange(0.1, 2.1, 0.1):
                threshold = round(threshold, 2)
                wbt.adaptive_filter(
                    i = tmp_path, 
                    output = output_path, 
                    filterx=filt_xy, 
                    filtery=filt_xy, 
                    threshold=threshold
                )

                with rasterio.open(output_path, 'r') as ds:
                    data_filt = ds.read()
                    data_filt = data_filt[0]

                if abs(np.mean(np.subtract(data_clear, data_filt))) < min_mean:
                    best_filter.update({noisy_dem : ['AdaptiveFilter', 5, 5, threshold]})
                    min_mean = abs(np.mean(np.subtract(data_clear, data_filt)))

            file.write('\t' + f'AdaptiveFilter: {filt_xy} * {filt_xy}, {threshold}. ' + \
                       f'mean = {np.mean(np.subtract(data_clear, data_filt))}' + '\n')

        # - - -
        #OlympicFilter
        for filt_xy in [3, 5, 7]:
            wbt.olympic_filter(
                i=tmp_path, 
                output=output_path, 
                filterx=filt_xy, 
                filtery=filt_xy
            )

            with rasterio.open(output_path, 'r') as ds:
                data_filt = ds.read()
                data_filt = data_filt[0]

            if abs(np.mean(np.subtract(data_clear, data_filt))) < min_mean:
                best_filter.update({noisy_dem : ['OlympicFilter', 5, 5]})
                min_mean = abs(np.mean(np.subtract(data_clear, data_filt)))

            file.write('\t' + f'OlympicFilter: {filt_xy} * {filt_xy}. ' + \
                       f'mean = {np.mean(np.subtract(data_clear, data_filt))}' + '\n')
    
        
end_time = time.time()
print(f'\n\nElapsed time: {(end_time - start_time)/60}')
        
best_filter

.\whitebox_tools.exe --run="MeanFilter" --wd=".\" --input='C:\Users\sasha\abstract_surfaces\surfaces\noisy\\hemicylinder_n_05.tif' --output='C:\Users\sasha\abstract_surfaces\surfaces\current_hemicylinder.tif' --filterx=3 --filtery=3 -v --compress_rasters=False

****************************
* Welcome to MeanFilter    *
* Powered by WhiteboxTools *
* www.whiteboxgeo.com      *
****************************
Reading data...
Creating integral images: 0%
Creating integral images: 1%
Creating integral images: 2%
Creating integral images: 3%
Creating integral images: 4%
Creating integral images: 5%
Creating integral images: 6%
Creating integral images: 7%
Creating integral images: 8%
Creating integral images: 10%
Creating integral images: 11%
Creating integral images: 12%
Creating integral images: 13%
Creating integral images: 14%
Creating integral images: 15%
Creating integral images: 16%
Creating integral images: 17%
Creating integral images: 19%
Creating integral images: 20%
Creating integra

Progress: 52%
Progress: 53%
Progress: 55%
Progress: 56%
Progress: 57%
Progress: 58%
Progress: 59%
Progress: 60%
Progress: 61%
Progress: 62%
Progress: 64%
Progress: 65%
Progress: 66%
Progress: 67%
Progress: 68%
Progress: 69%
Progress: 70%
Progress: 71%
Progress: 73%
Progress: 74%
Progress: 75%
Progress: 76%
Progress: 77%
Progress: 78%
Progress: 79%
Progress: 80%
Progress: 82%
Progress: 83%
Progress: 84%
Progress: 85%
Progress: 86%
Progress: 87%
Progress: 88%
Progress: 89%
Progress: 91%
Progress: 92%
Progress: 93%
Progress: 94%
Progress: 95%
Progress: 96%
Progress: 97%
Progress: 98%
Progress: 100%
Saving data...
Output file written
Elapsed Time (excluding I/O): 0.1s
.\whitebox_tools.exe --run="MeanFilter" --wd=".\" --input='C:\Users\sasha\abstract_surfaces\surfaces\noisy\\hemicylinder_n_05.tif' --output='C:\Users\sasha\abstract_surfaces\surfaces\current_hemicylinder.tif' --filterx=7 --filtery=7 -v --compress_rasters=False

****************************
* Welcome to MeanFilter    *
* Power

Performing analysis: 47%
Performing analysis: 48%
Performing analysis: 49%
Performing analysis: 50%
Performing analysis: 51%
Performing analysis: 52%
Performing analysis: 53%
Performing analysis: 55%
Performing analysis: 56%
Performing analysis: 57%
Performing analysis: 58%
Performing analysis: 59%
Performing analysis: 60%
Performing analysis: 61%
Performing analysis: 62%
Performing analysis: 64%
Performing analysis: 65%
Performing analysis: 66%
Performing analysis: 67%
Performing analysis: 68%
Performing analysis: 69%
Performing analysis: 70%
Performing analysis: 71%
Performing analysis: 73%
Performing analysis: 74%
Performing analysis: 75%
Performing analysis: 76%
Performing analysis: 77%
Performing analysis: 78%
Performing analysis: 79%
Performing analysis: 80%
Performing analysis: 82%
Performing analysis: 83%
Performing analysis: 84%
Performing analysis: 85%
Performing analysis: 86%
Performing analysis: 87%
Performing analysis: 88%
Performing analysis: 89%
Performing analysis: 91%


Performing analysis: 23%
Performing analysis: 24%
Performing analysis: 25%
Performing analysis: 26%
Performing analysis: 28%
Performing analysis: 29%
Performing analysis: 30%
Performing analysis: 31%
Performing analysis: 32%
Performing analysis: 33%
Performing analysis: 34%
Performing analysis: 35%
Performing analysis: 37%
Performing analysis: 38%
Performing analysis: 39%
Performing analysis: 40%
Performing analysis: 41%
Performing analysis: 42%
Performing analysis: 43%
Performing analysis: 44%
Performing analysis: 46%
Performing analysis: 47%
Performing analysis: 48%
Performing analysis: 49%
Performing analysis: 50%
Performing analysis: 51%
Performing analysis: 52%
Performing analysis: 53%
Performing analysis: 55%
Performing analysis: 56%
Performing analysis: 57%
Performing analysis: 58%
Performing analysis: 59%
Performing analysis: 60%
Performing analysis: 61%
Performing analysis: 62%
Performing analysis: 64%
Performing analysis: 65%
Performing analysis: 66%
Performing analysis: 67%


Calculating integral images: 42%
Calculating integral images: 43%
Calculating integral images: 44%
Calculating integral images: 46%
Calculating integral images: 47%
Calculating integral images: 48%
Calculating integral images: 49%
Calculating integral images: 50%
Calculating integral images: 51%
Calculating integral images: 52%
Calculating integral images: 53%
Calculating integral images: 55%
Calculating integral images: 56%
Calculating integral images: 57%
Calculating integral images: 58%
Calculating integral images: 59%
Calculating integral images: 60%
Calculating integral images: 61%
Calculating integral images: 62%
Calculating integral images: 64%
Calculating integral images: 65%
Calculating integral images: 66%
Calculating integral images: 67%
Calculating integral images: 68%
Calculating integral images: 69%
Calculating integral images: 70%
Calculating integral images: 71%
Calculating integral images: 73%
Calculating integral images: 74%
Calculating integral images: 75%
Calculatin

...

Calculating integral images: 83%
Calculating integral images: 84%
Calculating integral images: 85%
Calculating integral images: 86%
Calculating integral images: 87%
Calculating integral images: 88%
Calculating integral images: 89%
Calculating integral images: 90%
Calculating integral images: 91%
Calculating integral images: 92%
Calculating integral images: 93%
Calculating integral images: 94%
Calculating integral images: 95%
Calculating integral images: 96%
Calculating integral images: 97%
Calculating integral images: 98%
Calculating integral images: 99%
Calculating integral images: 100%
Progress: 0%
Progress: 1%
Progress: 2%
Progress: 3%
Progress: 4%
Progress: 5%
Progress: 6%
Progress: 7%
Progress: 8%
Progress: 9%
Progress: 10%
Progress: 11%
Progress: 12%
Progress: 13%
Progress: 14%
Progress: 15%
Progress: 16%
Progress: 17%
Progress: 18%
Progress: 19%
Progress: 20%
Progress: 21%
Progress: 22%
Progress: 23%
Progress: 24%
Progress: 25%
Progress: 26%
Progress: 27%
Progress: 28%
Progress:

Calculating integral images: 14%
Calculating integral images: 15%
Calculating integral images: 16%
Calculating integral images: 17%
Calculating integral images: 18%
Calculating integral images: 19%
Calculating integral images: 20%
Calculating integral images: 21%
Calculating integral images: 22%
Calculating integral images: 23%
Calculating integral images: 24%
Calculating integral images: 25%
Calculating integral images: 26%
Calculating integral images: 27%
Calculating integral images: 28%
Calculating integral images: 29%
Calculating integral images: 30%
Calculating integral images: 31%
Calculating integral images: 32%
Calculating integral images: 33%
Calculating integral images: 34%
Calculating integral images: 35%
Calculating integral images: 36%
Calculating integral images: 37%
Calculating integral images: 38%
Calculating integral images: 39%
Calculating integral images: 40%
Calculating integral images: 41%
Calculating integral images: 42%
Calculating integral images: 43%
Calculatin

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Progress: 11%
Progress: 12%
Progress: 13%
Progress: 14%
Progress: 15%
Progress: 16%
Progress: 17%
Progress: 18%
Progress: 19%
Progress: 20%
Progress: 21%
Progress: 22%
Progress: 23%
Progress: 24%
Progress: 25%
Progress: 26%
Progress: 27%
Progress: 28%
Progress: 29%
Progress: 30%
Progress: 31%
Progress: 32%
Progress: 33%
Progress: 34%
Progress: 35%
Progress: 36%
Progress: 37%
Progress: 38%
Progress: 39%
Progress: 40%
Progress: 41%
Progress: 42%
Progress: 43%
Progress: 44%
Progress: 45%
Progress: 46%
Progress: 47%
Progress: 48%
Progress: 49%
Progress: 50%
Progress: 51%
Progress: 52%
Progress: 53%
Progress: 54%
Progress: 55%
Progress: 56%
Progress: 57%
Progress: 58%
Progress: 59%
Progress: 60%
Progress: 61%
Progress: 62%
Progress: 63%
Progress: 64%
Progress: 65%
Progress: 66%
Progress: 67%
Progress: 68%
Progress: 69%
Progress: 70%
Progress: 71%
Progress: 72%
Progress: 73%
Progress: 74%
Progress: 75%
Progress: 76%
Progress: 77%
Progress: 78%
Progress: 79%
Progress: 80%
Progress: 81%
Progre

{'hemicylinder_n_05.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_n_1.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_n_2.tif': ['MedianFilter', 5, 5],
 'hemicylinder_un_05.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_un_1.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_un_2.tif': ['MedianFilter', 5, 5],
 'hemisphere_n_05.tif': ['OlympicFilter', 5, 5],
 'hemisphere_n_1.tif': ['OlympicFilter', 5, 5],
 'hemisphere_n_2.tif': ['OlympicFilter', 5, 5],
 'hemisphere_un_05.tif': ['OlympicFilter', 5, 5],
 'hemisphere_un_1.tif': ['OlympicFilter', 5, 5],
 'hemisphere_un_2.tif': ['MedianFilter', 7, 7],
 'inclined_n_05.tif': ['AdaptiveFilter', 5, 5, 2.0],
 'inclined_n_1.tif': ['AdaptiveFilter', 5, 5, 1.5],
 'inclined_n_2.tif': ['AdaptiveFilter', 5, 5, 1.4],
 'inclined_un_05.tif': ['AdaptiveFilter', 5, 5, 1.7],
 'inclined_un_1.tif': ['AdaptiveFilter', 5, 5, 2.0],
 'inclined_un_2.tif': ['AdaptiveFilter', 5, 5, 1.6],
 'paraboloid_n_05.tif': ['AdaptiveFilter', 5, 5, 1.9],
 'paraboloid_n_1.tif': ['Adaptive

In [35]:
best_filter['hemicylinder_n_05.tif'][0]

'AdaptiveFilter'

In [40]:
best_filter

{'hemicylinder_n_05.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_n_1.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_n_2.tif': ['MedianFilter', 5, 5],
 'hemicylinder_un_05.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_un_1.tif': ['OlympicFilter', 5, 5],
 'hemicylinder_un_2.tif': ['MedianFilter', 5, 5],
 'hemisphere_n_05.tif': ['OlympicFilter', 5, 5],
 'hemisphere_n_1.tif': ['OlympicFilter', 5, 5],
 'hemisphere_n_2.tif': ['OlympicFilter', 5, 5],
 'hemisphere_un_05.tif': ['OlympicFilter', 5, 5],
 'hemisphere_un_1.tif': ['OlympicFilter', 5, 5],
 'hemisphere_un_2.tif': ['MedianFilter', 7, 7],
 'inclined_n_05.tif': ['AdaptiveFilter', 5, 5, 2.0],
 'inclined_n_1.tif': ['AdaptiveFilter', 5, 5, 1.5],
 'inclined_n_2.tif': ['AdaptiveFilter', 5, 5, 1.4],
 'inclined_un_05.tif': ['AdaptiveFilter', 5, 5, 1.7],
 'inclined_un_1.tif': ['AdaptiveFilter', 5, 5, 2.0],
 'inclined_un_2.tif': ['AdaptiveFilter', 5, 5, 1.6],
 'paraboloid_n_05.tif': ['AdaptiveFilter', 5, 5, 1.9],
 'paraboloid_n_1.tif': ['Adaptive